# Libraries import + Input Data

In [ ]:
#if you're using colab, connect to the google drive
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
#create a "data" folder and upload "MTBLS90.xlsx" file in it
home = '/content/drive/MyDrive/data/' 
file = 'MTBLS90.xlsx'

In [ ]:
pip install https://github.com/cimcb/cimcb/archive/master.zip

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached https://github.com/cimcb/cimcb/archive/master.zip
  Preparing metadata (setup.py) ... done


In [ ]:
import cimcb as cb
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

print('All packages successfully loaded')

All packages successfully loaded


In [ ]:
# load and summarize the dataset
from pandas import read_csv
# load the dataset
DataTable,PeakTable = cb.utils.load_dataXL(home + file, DataSheet='Data', PeakSheet='Peak') 

Loadings PeakFile: Peak
Loadings DataFile: Data


/usr/local/lib/python3.10/dist-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/usr/local/lib/python3.10/dist-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


Data Table & Peak Table is suitable.
TOTAL SAMPLES: 968 TOTAL PEAKS: 189
Done!


In [ ]:
print(DataTable.describe())

              Idx       Class          M1          M2          M3          M4  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean   484.500000    0.501033   15.100309   14.588205   12.993140   11.916599   
std    279.581831    0.500257    0.287554    0.333544    1.187480    0.783079   
min      1.000000    0.000000   14.186670   13.273450    8.222473    6.885203   
25%    242.750000    0.000000   14.915625   14.358245   12.116768   11.428658   
50%    484.500000    1.000000   15.108960   14.581345   12.749361   11.966888   
75%    726.250000    1.000000   15.298583   14.807030   14.057987   12.426928   
max    968.000000    1.000000   15.994000   16.419860   16.143734   14.050150   

               M5          M6          M7          M8  ...        M180  \
count  968.000000  968.000000  968.000000  968.000000  ...  968.000000   
mean    11.538797   15.371513   17.197264   12.128846  ...   21.295237   
std      0.484311    0.408534    0.411065    0.6

In [ ]:
DataTable.isna().sum().sum()

0

We do not have any null values in the dataframe

In [ ]:
(DataTable.iloc[:, 3:] == 0).sum().sum()

0

We do not have any zeroes in columns M1, M2,...., M189 in the dataframe 

In [ ]:
print("Total number of values = ",DataTable.shape[0]*DataTable.shape[1])

Total number of values =  186824


#Making the data “dirty”. 


In [ ]:
#returns n% random indices from the dataframe df
def get_random_indices(df,n): 
  import random

  ind_arr = [(row, col) for row in range(df.shape[0]) for col in range(df.shape[1])]

  indices = []
  for row, col in random.sample(ind_arr, int(round((n/100)*len(ind_arr)))):
    indices.append([row, col])

  return indices

In [ ]:
#making the data dirty

#Strategy 1 : Remove 10% of the values
ind = get_random_indices(DataTable, 10)

DataTable_st1 = DataTable.copy()

for i in ind:
  DataTable_st1.iloc[i[0], i[1]] = np.NaN

print(DataTable_st1.head()) 

#check if number of values are 10% of the original dataframe
print("Number of NaN = ",DataTable_st1.isna().sum().sum())

   Idx      SampleID  Class     Sex        M1        M2         M3         M4  \
1  1.0           NaN    0.0  Female  14.98474  14.49947  12.097435  12.043818   
2  2.0  subject_1525    1.0     NaN  15.17667  14.50172  12.363773  12.240458   
3  3.0  subject_1527    1.0    Male       NaN  14.41941        NaN  11.234959   
4  NaN  subject_1528    1.0    Male  15.12638  14.75630  13.001426  12.640496   
5  NaN  subject_1529    1.0     NaN  15.20272  14.48083  12.392280  10.779516   

          M5        M6  ...      M180      M181      M182      M183      M184  \
1  11.436392  16.07217  ...  20.70097  20.19814       NaN  21.09176  16.46404   
2  11.577436  14.93265  ...  21.68605       NaN  21.25777  20.53935  16.33413   
3  11.199970  15.22600  ...  20.46320  20.34297  21.34793  20.81883  16.44281   
4  11.244146  14.78994  ...  21.36879  20.93957  21.09719  20.82021  16.27483   
5  10.968423       NaN  ...  20.80482  19.82493  20.84250  20.31349  16.33279   

        M185      M186    

In [ ]:
print(DataTable_st1.describe()) 

              Idx       Class          M1          M2          M3          M4  \
count  871.000000  859.000000  884.000000  868.000000  854.000000  869.000000   
mean   488.354765    0.501746   15.103041   14.588368   12.983130   11.919116   
std    279.930721    0.500288    0.284702    0.333452    1.184770    0.784640   
min      1.000000    0.000000   14.186670   13.273450    8.222473    6.885203   
25%    245.500000    0.000000   14.923602   14.358195   12.102734   11.432794   
50%    490.000000    1.000000   15.116825   14.577435   12.727922   11.975292   
75%    729.500000    1.000000   15.299375   14.808430   14.057310   12.434987   
max    968.000000    1.000000   15.994000   16.419860   16.143734   13.926532   

               M5          M6          M7          M8  ...        M180  \
count  871.000000  873.000000  875.000000  886.000000  ...  870.000000   
mean    11.539068   15.376575   17.200974   12.120621  ...   21.299545   
std      0.487517    0.406346    0.410428    0.6

In [ ]:
print(DataTable_st1.head()) 

   Idx      SampleID  Class     Sex        M1        M2         M3         M4  \
1  1.0           NaN    0.0  Female  14.98474  14.49947  12.097435  12.043818   
2  2.0  subject_1525    1.0     NaN  15.17667  14.50172  12.363773  12.240458   
3  3.0  subject_1527    1.0    Male       NaN  14.41941        NaN  11.234959   
4  NaN  subject_1528    1.0    Male  15.12638  14.75630  13.001426  12.640496   
5  NaN  subject_1529    1.0     NaN  15.20272  14.48083  12.392280  10.779516   

          M5        M6  ...      M180      M181      M182      M183      M184  \
1  11.436392  16.07217  ...  20.70097  20.19814       NaN  21.09176  16.46404   
2  11.577436  14.93265  ...  21.68605       NaN  21.25777  20.53935  16.33413   
3  11.199970  15.22600  ...  20.46320  20.34297  21.34793  20.81883  16.44281   
4  11.244146  14.78994  ...  21.36879  20.93957  21.09719  20.82021  16.27483   
5  10.968423       NaN  ...  20.80482  19.82493  20.84250  20.31349  16.33279   

        M185      M186    

Nan can be observed at random locations and the number of Nan are 10% of the original size of the *dataset*

In [ ]:
#Strategy 2 : Remove 50% of the values
ind = get_random_indices(DataTable, 50)

DataTable_st2 = DataTable.copy()

for i in ind:
  DataTable_st2.iloc[i[0], i[1]] = np.NaN

print(DataTable_st2.head())
print("Number of NaN = ",DataTable_st2.isna().sum().sum())

   Idx      SampleID  Class   Sex        M1        M2         M3         M4  \
1  1.0           NaN    NaN   NaN       NaN  14.49947  12.097435  12.043818   
2  2.0  subject_1525    1.0   NaN       NaN  14.50172        NaN        NaN   
3  3.0           NaN    1.0  Male       NaN  14.41941  12.510494        NaN   
4  NaN           NaN    1.0  Male       NaN       NaN        NaN        NaN   
5  5.0           NaN    1.0   NaN  15.20272  14.48083  12.392280        NaN   

          M5  M6  ...      M180      M181      M182      M183      M184  \
1        NaN NaN  ...  20.70097       NaN  21.28179  21.09176  16.46404   
2  11.577436 NaN  ...  21.68605  20.51608       NaN  20.53935       NaN   
3        NaN NaN  ...       NaN       NaN       NaN       NaN       NaN   
4        NaN NaN  ...       NaN       NaN  21.09719  20.82021  16.27483   
5        NaN NaN  ...       NaN  19.82493       NaN       NaN       NaN   

        M185      M186      M187      M188      M189  
1        NaN       

Nan can be observed at random locations and the number of Nan are 50% of the original size of the *dataset*

In [ ]:
DataTable_st2.describe()

Idx       Class          M1          M2          M3          M4  \
count  499.000000  489.000000  475.000000  504.000000  461.000000  475.000000   
mean   490.763527    0.517382   15.098062   14.603486   13.025693   11.878050   
std    274.442692    0.500209    0.291772    0.340105    1.197048    0.757708   
min      1.000000    0.000000   14.256410   13.647980    8.222473    8.917743   
25%    263.500000    0.000000   14.906890   14.357813   12.177484   11.394671   
50%    479.000000    1.000000   15.110350   14.604325   12.754738   11.902164   
75%    719.000000    1.000000   15.298095   14.823420   14.073974   12.338793   
max    968.000000    1.000000   15.912750   15.599460   15.852318   14.050150   

               M5          M6          M7          M8  ...        M180  \
count  452.000000  484.000000  452.000000  502.000000  ...  481.000000   
mean    11.521286   15.371052   17.172637   12.136972  ...   21.299532   
std      0.497754    0.417477    0.415093    0.697900  ...    0.534073   
min      8.545572   14.177460   15.627670    9.167940  ...   19.663210   
25%     11.277193   15.072083   16.926205   12.007851  ...   20.960170   
50%     11.572689   15.337440   17.156965   12.103236  ...   21.335380   
75%     11.818734   15.646162   17.455472   12.224063  ...   21.652940   
max     12.667022   16.954200   18.310400   16.947787  ...   22.564840   

             M181        M182        M183        M184        M185        M186  \
count  484.000000  485.000000  453.000000  464.000000  496.000000  509.000000   
mean    20.569602   21.208431   20.434499   15.981982   11.635630   17.640645   
std      0.627466    0.436594    0.564562    0.556670    0.671057    0.398901   
min     18.461300   18.853580   18.729910   12.034610    9.131690   16.251900   
25%     20.179347   20.925780   20.057570   15.677843   11.190557   17.384710   
50%     20.530770   21.210710   20.459100   16.030175   11.676588   17.661070   
75%     21.011118   21.514070   20.828700   16.356713   12.113268   17.922520   
max     22.061630   22.527540   22.153810   17.930610   14.766459   18.883270   

             M187        M188        M189  
count  527.000000  483.000000  508.000000  
mean    19.268385   19.346250   12.026091  
std      0.457718    0.591318    0.490098  
min     17.564340   16.158640   10.034670  
25%     19.026260   18.925140   11.746198  
50%     19.328600   19.311060   12.051990  
75%     19.576900   19.745600   12.357967  
max     20.323180   21.080430   13.521310  

[8 rows x 191 columns]

In [ ]:
#Strategy 3 : Change 10% of the values
ind = get_random_indices(DataTable, 10)

DataTable_st3 = DataTable.copy()
temp = 0
for i in ind:
  noise = np.random.normal(0, 20) 
  if isinstance(DataTable_st3.iloc[i[0], i[1]], str):
    DataTable_st3.iloc[i[0], i[1]] = str(noise)
  else: 
    if(temp%2 == 0):
      DataTable_st3.iloc[i[0], i[1]] = DataTable_st3.iloc[i[0], i[1]] + noise
    else:
      DataTable_st3.iloc[i[0], i[1]] = DataTable_st3.iloc[i[0], i[1]] - noise
  temp+=1

print(DataTable_st3.describe())

               Idx       Class          M1          M2          M3  \
count   968.000000  968.000000  968.000000  968.000000  968.000000   
mean    484.316384    0.649421   15.088559   14.871726   13.229712   
std     279.899417    6.527270    5.546958    5.504212    5.883846   
min     -44.990616  -51.219757  -31.711937  -26.260356  -28.066182   
25%     242.750000    0.000000   14.881820   14.338043   12.070757   
50%     485.275878    0.067377   15.095755   14.589085   12.759811   
75%     726.250000    1.000000   15.302535   14.833293   14.120324   
max    1000.083549   40.909829   50.780279   65.829629   63.857087   

               M4          M5          M6          M7          M8  ...  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  ...   
mean    12.040389   11.540949   15.656018   17.120794   12.025885  ...   
std      5.819073    6.508635    5.992267    6.231190    5.116713  ...   
min    -28.196247  -37.467875  -41.377550  -36.624087  -35.666105  ...   

In [ ]:
#Strategy 4 : Change 50% of the values
ind = get_random_indices(DataTable, 50)

DataTable_st4 = DataTable.copy()
temp = 0
for i in ind:
  noise = np.random.normal(0, 20) 
  if isinstance(DataTable_st4.iloc[i[0], i[1]], str):
    DataTable_st4.iloc[i[0], i[1]] = str(noise)
  else: 
    if(temp%2 == 0):
      DataTable_st4.iloc[i[0], i[1]] = DataTable_st4.iloc[i[0], i[1]] + noise
    else:
      DataTable_st4.iloc[i[0], i[1]] = DataTable_st4.iloc[i[0], i[1]] - noise
  temp+=1

print(DataTable_st4.describe())

              Idx       Class          M1          M2          M3          M4  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean   484.613309    1.192617   15.047394   14.456723   12.972992   11.929286   
std    279.630573   14.666728   14.403478   14.143555   14.486696   13.593463   
min    -38.346491  -63.411646  -42.277269  -44.299910  -40.747115  -40.089332   
25%    238.750314    0.000000   14.535258   14.074995   11.207131   10.598517   
50%    479.934457    0.928433   15.095850   14.610360   12.771500   11.989309   
75%    730.500000    1.176631   15.703368   15.255861   15.243418   13.172577   
max    979.320969   60.881753   72.047449   72.659821   69.639009   65.806094   

               M5          M6          M7          M8  ...        M180  \
count  968.000000  968.000000  968.000000  968.000000  ...  968.000000   
mean    11.098277   15.801334   17.244897   12.071741  ...   20.799479   
std     12.971548   13.855028   14.376379   14.0

Difference can be observed in the description of the dataset because of the imputed noise

#Cleaning the data

####**Analyzing the data**

In [ ]:
na_count_st1 = DataTable_st1.isna().sum() #number of nulls in each column for strategy 1
na_count_st1

Idx          89
SampleID     96
Class        88
Sex         112
M1           97
           ... 
M185        109
M186         92
M187         90
M188        104
M189        104
Length: 193, dtype: int64

In [ ]:
na_count_st2 = DataTable_st2.isna().sum() #number of nulls in each column for strategy 2
na_count_st2

Idx         483
SampleID    468
Class       499
Sex         498
M1          491
           ... 
M185        458
M186        483
M187        484
M188        508
M189        465
Length: 193, dtype: int64

In [ ]:
DataTable.shape

(968, 193)

In [ ]:
 DataTable_st1[DataTable_st1.isna().any(axis=1)].shape[0] #number of rows with at least one null value for strategy 1

968

In [ ]:
 DataTable_st2[DataTable_st2.isna().any(axis=1)].shape[0] #number of rows with at least one null value for strategy 2


968

Every row has at least one NaN for dataframe with both 50% NaN and 10% NaN. Dropping the rows with null will leave us with empty dataframes for both the cases

###**Replacing null with some statistical measure**

####mputing the metabolites columns with the mean for each of the columns. Then later, trying linear regression on these metabolites column, the target "Class" column having NaN. The rest of the clumns are not important for the analysis and will not be used in any of the models, therefore no imputations were made to them.

In [ ]:
#for dataset with 10% null values
DataTable_st1_mean = DataTable_st1.copy()
DataTable_st1_mean.iloc[:, 4:] = DataTable_st1_mean.iloc[:, 4:].fillna(DataTable_st1_mean.iloc[:, 4:].mean()) #replace with mean
DataTable_st1_mean

Idx      SampleID  Class     Sex         M1         M2         M3  \
1      1.0  subject_1524    0.0  Female  14.984740  14.499470  12.986745   
2      2.0  subject_1525    1.0    Male  15.176670  14.501720  12.363773   
3      3.0  subject_1527    1.0     NaN  15.359340  14.584378  12.510494   
4      4.0  subject_1528    1.0    Male  15.126380  14.756300  13.001426   
5      5.0  subject_1529    1.0    Male  15.202720  14.480830  12.392280   
..     ...           ...    ...     ...        ...        ...        ...   
964  964.0  subject_2510    0.0  Female  15.097652  14.697530  13.537908   
965  965.0  subject_2511    0.0  Female  15.342130  14.325000  13.069032   
966  966.0  subject_2512    NaN    Male  15.116860  13.939520  11.018040   
967  967.0  subject_2513    1.0    Male  15.029150  14.022260  12.910623   
968  968.0  subject_2514    0.0  Female  15.223080  14.701110  14.087563   

            M4         M5         M6  ...       M180       M181       M182  \
1    12.043818  11.535524  16.072170  ...  20.700970  20.198140  21.281790   
2    11.914075  11.577436  14.932650  ...  21.309762  20.567563  21.257770   
3    11.234959  11.199970  15.226000  ...  20.463200  20.342970  21.188288   
4    12.640496  11.244146  14.789940  ...  21.368790  20.939570  21.097190   
5    10.779516  10.968423  15.366408  ...  20.804820  19.824930  20.842500   
..         ...        ...        ...  ...        ...        ...        ...   
964  11.020669  11.606563  15.733280  ...  21.176070  20.621250  21.492000   
965  12.251669  11.857594  15.124550  ...  22.009020  21.164240  21.060300   
966  12.078832  12.022111  15.234820  ...  21.773740  21.128520  21.283930   
967  11.196043  12.320042  15.222310  ...  20.625480  20.050190  21.188288   
968  13.369055  11.730996  15.204020  ...  21.393570  20.905350  21.107540   

          M183      M184       M185      M186      M187      M188       M189  
1    21.091760  16.46404  12.269896  17.29323  19.81546  19.35259  12.716080  
2    20.539350  16.33413  12.031267  18.08144  19.96693  19.50694  13.208910  
3    20.431962  16.44281  12.679043  17.24765  20.01505  20.34058  12.982100  
4    20.820210  16.27483  12.323163  17.72392  19.27534  19.18157  12.410390  
5    20.313490  16.33279  12.352881  17.59348  19.88594  18.66284  12.374790  
..         ...       ...        ...       ...       ...       ...        ...  
964  20.674140  15.24188  10.707697  17.23263  18.98958  20.10754  12.027166  
965  20.260110  15.97133  11.637138  17.89835  19.47135  20.10864  12.263100  
966  20.854590  16.45625  11.637138  17.46066  19.80941  19.70745  12.027166  
967  20.900290  15.86242  11.232866  17.20357  19.44558  19.05356  11.897410  
968  20.271260  15.68142  10.917716  17.77879  19.32727  19.25712  11.949190  

[968 rows x 193 columns]

In [ ]:
#for variable "Class", regression analysis for imputation

#making a temporary dataframe on which regression will happen
DataTable_st1_mean_temp = DataTable_st1_mean.copy()
DataTable_st1_mean_temp = DataTable_st1_mean_temp.dropna(subset=['Class']) #97 rows with Class as NaN will be dropped

# Select the features that have the highest correlation with "Class"
correlations = DataTable_st1_mean_temp.corr()["Class"].abs().sort_values(ascending=False)

# Top  most correlated features with the target variable
print(correlations[1:6])

M142    0.381873
M10     0.369033
M141    0.364278
M2      0.322733
M152    0.319946
Name: Class, dtype: float64


<ipython-input-25-6786ee44ec3a>:8: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  correlations = DataTable_st1_mean_temp.corr()["Class"].abs().sort_values(ascending=False)


In [ ]:
#Linear regression model
from sklearn.linear_model import LinearRegression

# Extract PeakList 
PeakList = ['M142','M141','M10','M2','M147']  

# Select Subset of Data 
DataTable2 = DataTable[(DataTable_st1_mean.Class == 1) | (DataTable_st1_mean.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean  

#Linear Regression model
reg = LinearRegression().fit(XTrainKnn, YTrain)
reg.score(XTestKnn, YTest)

0.2241968337880652

In [ ]:
DataTable_st1_mean = DataTable_st1_mean.dropna(subset=['Class'])
DataTable_st1_mean.shape

(880, 193)

The score came out very low, so it is rather better to drop these columns than to impute any unreliable values into the target class variable. Earlier, the analysis was done on all metabolites and the score was low even for that.

In [ ]:
#for dataset with 50% null values
DataTable_st2_mean = DataTable_st2.copy()
DataTable_st2_mean.iloc[:, 4:] = DataTable_st2_mean.iloc[:, 4:].fillna(DataTable_st2_mean.iloc[:, 4:].mean()) #replace with mean
DataTable_st2_mean

Idx      SampleID  Class     Sex         M1         M2         M3  \
1    1.0           NaN    NaN     NaN  15.093364  14.499470  12.959470   
2    2.0           NaN    NaN    Male  15.093364  14.501720  12.959470   
3    NaN  subject_1527    NaN     NaN  15.359340  14.419410  12.959470   
4    NaN           NaN    NaN    Male  15.126380  14.756300  13.001426   
5    5.0  subject_1529    NaN     NaN  15.093364  14.577286  12.959470   
..   ...           ...    ...     ...        ...        ...        ...   
964  NaN           NaN    NaN     NaN  15.526260  14.697530  13.537908   
965  NaN           NaN    NaN  Female  15.093364  14.325000  13.069032   
966  NaN           NaN    1.0     NaN  15.093364  13.939520  11.018040   
967  NaN           NaN    NaN     NaN  15.029150  14.577286  12.910623   
968  NaN  subject_2514    0.0  Female  15.093364  14.577286  14.087563   

            M4         M5         M6  ...      M180       M181       M182  \
1    11.937840  11.436392  15.377125  ...  20.70097  20.566092  21.209816   
2    12.240458  11.529857  15.377125  ...  21.30473  20.516080  21.209816   
3    11.234959  11.529857  15.377125  ...  20.46320  20.342970  21.209816   
4    11.937840  11.529857  14.789940  ...  21.36879  20.566092  21.209816   
5    11.937840  10.968423  15.377125  ...  20.80482  19.824930  20.842500   
..         ...        ...        ...  ...       ...        ...        ...   
964  11.020669  11.606563  15.377125  ...  21.30473  20.621250  21.492000   
965  12.251669  11.529857  15.377125  ...  22.00902  21.164240  21.060300   
966  11.937840  11.529857  15.234820  ...  21.77374  21.128520  21.209816   
967  11.196043  11.529857  15.222310  ...  20.62548  20.050190  21.311810   
968  11.937840  11.529857  15.204020  ...  21.30473  20.905350  21.107540   

          M183       M184       M185       M186       M187       M188  \
1    20.465801  16.464040  12.269896  17.650836  19.815460  19.352590   
2    20.539350  15.986495  12.031267  18.081440  19.251903  19.285485   
3    20.465801  15.986495  12.679043  17.247650  20.015050  19.285485   
4    20.465801  16.274830  12.323163  17.650836  19.575220  19.181570   
5    20.313490  15.986495  11.649721  17.650836  19.885940  18.662840   
..         ...        ...        ...        ...        ...        ...   
964  20.674140  15.241880  11.649721  17.650836  18.989580  19.285485   
965  20.260110  15.986495  11.649721  17.898350  19.471350  20.108640   
966  20.465801  15.986495  11.649721  17.650836  19.251903  19.707450   
967  20.900290  15.862420  11.232866  17.650836  19.445580  19.053560   
968  20.465801  15.681420  11.649721  17.650836  19.327270  19.285485   

          M189  
1    12.716080  
2    13.208910  
3    12.982100  
4    12.038459  
5    12.038459  
..         ...  
964  12.038459  
965  12.038459  
966  12.653960  
967  11.897410  
968  11.949190  

[968 rows x 193 columns]

In [ ]:
#for variable "Class", the values will be imputed using regression

#making a temporary dataframe on which regression will happen
DataTable_st2_mean_temp = DataTable_st2_mean.copy()
DataTable_st2_mean_temp = DataTable_st2_mean_temp.dropna(subset=['Class'])

# Select the features that have the highest correlation with "Class"
correlations = DataTable_st2_mean_temp.corr()["Class"].abs().sort_values(ascending=False)

# Top  most correlated features with the target variable
print(correlations[1:6])

M141    0.351286
M142    0.298966
M15     0.268154
M28     0.256058
M35     0.241755
Name: Class, dtype: float64


<ipython-input-29-c4a582db9187>:8: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  correlations = DataTable_st2_mean_temp.corr()["Class"].abs().sort_values(ascending=False)


In [ ]:
#Linear regression model
from sklearn.linear_model import LinearRegression

# Extract PeakList 
PeakList = ['M147','M10','M141','M2','M171']  

# Select Subset of Data 
DataTable2 = DataTable[(DataTable_st2_mean.Class == 1) | (DataTable_st2_mean.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean  

#Linear Regression model
reg = LinearRegression().fit(XTrainKnn, YTrain)
reg.score(XTestKnn, YTest)

0.24090565399831187

In [ ]:
DataTable_st2_mean = DataTable_st2_mean.dropna(subset=['Class'])
DataTable_st2_mean.shape

(469, 193)

 Low regression score for strategy 2 as well. Therefore, dropping na columns would be preferred here as well even though half of the dataset will be lost that way.

####Imputing the metabolites columns with the median for each of the columns

Since we are aware that there are high chances of getting low scores for the regression for finding the values for class varible, thus we will simply drop the columns where class is nan.

In [ ]:
#for dataset with 10% null values
DataTable_st1_med = DataTable_st1.copy()
DataTable_st1_med.iloc[:, 4:] = DataTable_st1_med.iloc[:, 4:].fillna(DataTable_st1_med.iloc[:, 4:].median())
DataTable_st1_med

Idx      SampleID  Class     Sex        M1         M2         M3  \
1      1.0  subject_1524    0.0  Female  14.98474  14.499470  12.761965   
2      2.0  subject_1525    1.0    Male  15.17667  14.501720  12.363773   
3      3.0  subject_1527    1.0     NaN  15.35934  14.575565  12.510494   
4      4.0  subject_1528    1.0    Male  15.12638  14.756300  13.001426   
5      5.0  subject_1529    1.0    Male  15.20272  14.480830  12.392280   
..     ...           ...    ...     ...       ...        ...        ...   
964  964.0  subject_2510    0.0  Female  15.10397  14.697530  13.537908   
965  965.0  subject_2511    0.0  Female  15.34213  14.325000  13.069032   
966  966.0  subject_2512    NaN    Male  15.11686  13.939520  11.018040   
967  967.0  subject_2513    1.0    Male  15.02915  14.022260  12.910623   
968  968.0  subject_2514    0.0  Female  15.22308  14.701110  14.087563   

            M4         M5        M6  ...      M180      M181      M182  \
1    12.043818  11.571713  16.07217  ...  20.70097  20.19814  21.28179   
2    11.954739  11.577436  14.93265  ...  21.33956  20.55076  21.25777   
3    11.234959  11.199970  15.22600  ...  20.46320  20.34297  21.20157   
4    12.640496  11.244146  14.78994  ...  21.36879  20.93957  21.09719   
5    10.779516  10.968423  15.34276  ...  20.80482  19.82493  20.84250   
..         ...        ...       ...  ...       ...       ...       ...   
964  11.020669  11.606563  15.73328  ...  21.17607  20.62125  21.49200   
965  12.251669  11.857594  15.12455  ...  22.00902  21.16424  21.06030   
966  12.078832  12.022111  15.23482  ...  21.77374  21.12852  21.28393   
967  11.196043  12.320042  15.22231  ...  20.62548  20.05019  21.20157   
968  13.369055  11.730996  15.20402  ...  21.39357  20.90535  21.10754   

         M183      M184       M185      M186       M187      M188      M189  
1    21.09176  16.46404  12.269896  17.29323  19.815460  19.35259  12.71608  
2    20.53935  16.33413  12.031267  18.08144  19.966930  19.50694  13.20891  
3    20.45810  16.44281  12.679043  17.24765  20.015050  20.34058  12.98210  
4    20.82021  16.27483  12.323163  17.72392  19.339545  19.18157  12.41039  
5    20.31349  16.33279  12.352881  17.59348  19.885940  18.66284  12.37479  
..        ...       ...        ...       ...        ...       ...       ...  
964  20.67414  15.24188  10.707697  17.23263  18.989580  20.10754  12.05720  
965  20.26011  15.97133  11.656765  17.89835  19.471350  20.10864  12.26310  
966  20.85459  16.45625  11.656765  17.46066  19.809410  19.70745  12.05720  
967  20.90029  15.86242  11.232866  17.20357  19.445580  19.05356  11.89741  
968  20.27126  15.68142  10.917716  17.77879  19.327270  19.25712  11.94919  

[968 rows x 193 columns]

In [ ]:
#for variable "Class", the values will be imputed using regression

#making a temporary dataframe on which regression will happen
DataTable_st1_med_temp = DataTable_st1_med.copy()
DataTable_st1_med_temp = DataTable_st1_med_temp.dropna(subset=['Class'])

# Select the features that have the highest correlation with "Class"
correlations = DataTable_st1_med_temp.corr()["Class"].abs().sort_values(ascending=False)

# Top  most correlated features with the target variable
print(correlations[1:6])

M142    0.381777
M10     0.369005
M141    0.364277
M2      0.322863
M152    0.320017
Name: Class, dtype: float64


<ipython-input-33-6d04480df183>:8: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  correlations = DataTable_st1_med_temp.corr()["Class"].abs().sort_values(ascending=False)


In [ ]:
#Linear regression model
from sklearn.linear_model import LinearRegression

# Extract PeakList 
PeakList = ['M142','M141','M10','M2','M147']  

# Select Subset of Data 
DataTable2 = DataTable_st1_med_temp[(DataTable_st1_med_temp.Class == 1) | (DataTable_st1_med_temp.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean  

#Linear Regression model
reg = LinearRegression().fit(XTrainKnn, YTrain)
reg.score(XTestKnn, YTest)

0.2356332194889924

In [ ]:
DataTable_st1_med = DataTable_st1_med.dropna(subset=['Class'])
DataTable_st1_med.shape

(880, 193)

Class with NaN was dropped for strategy 1 with median imputations in for metabolites columns. The same will be done for startegy 2 because the results will most likely not improve


In [ ]:
#for dataset with 50% null values
DataTable_st2_med = DataTable_st2.copy()
DataTable_st2_med.iloc[:, 4:] = DataTable_st2_med.iloc[:, 4:].fillna(DataTable_st2_med.iloc[:, 4:].median())
DataTable_st2_med

Idx      SampleID  Class     Sex        M1         M2         M3  \
1    1.0           NaN    NaN     NaN  15.09165  14.499470  12.699393   
2    2.0           NaN    NaN    Male  15.09165  14.501720  12.699393   
3    NaN  subject_1527    NaN     NaN  15.35934  14.419410  12.699393   
4    NaN           NaN    NaN    Male  15.12638  14.756300  13.001426   
5    5.0  subject_1529    NaN     NaN  15.09165  14.572325  12.699393   
..   ...           ...    ...     ...       ...        ...        ...   
964  NaN           NaN    NaN     NaN  15.52626  14.697530  13.537908   
965  NaN           NaN    NaN  Female  15.09165  14.325000  13.069032   
966  NaN           NaN    1.0     NaN  15.09165  13.939520  11.018040   
967  NaN           NaN    NaN     NaN  15.02915  14.572325  12.910623   
968  NaN  subject_2514    0.0  Female  15.09165  14.572325  14.087563   

            M4         M5        M6  ...      M180      M181      M182  \
1    11.969920  11.436392  15.35395  ...  20.70097  20.53306  21.21007   
2    12.240458  11.575971  15.35395  ...  21.31663  20.51608  21.21007   
3    11.234959  11.575971  15.35395  ...  20.46320  20.34297  21.21007   
4    11.969920  11.575971  14.78994  ...  21.36879  20.53306  21.21007   
5    11.969920  10.968423  15.35395  ...  20.80482  19.82493  20.84250   
..         ...        ...       ...  ...       ...       ...       ...   
964  11.020669  11.606563  15.35395  ...  21.31663  20.62125  21.49200   
965  12.251669  11.575971  15.35395  ...  22.00902  21.16424  21.06030   
966  11.969920  11.575971  15.23482  ...  21.77374  21.12852  21.21007   
967  11.196043  11.575971  15.22231  ...  20.62548  20.05019  21.31181   
968  11.969920  11.575971  15.20402  ...  21.31663  20.90535  21.10754   

         M183      M184       M185      M186      M187       M188      M189  
1    20.51080  16.46404  12.269896  17.66347  19.81546  19.352590  12.71608  
2    20.53935  16.02301  12.031267  18.08144  19.30506  19.282875  13.20891  
3    20.51080  16.02301  12.679043  17.24765  20.01505  19.282875  12.98210  
4    20.51080  16.27483  12.323163  17.66347  19.57522  19.181570  12.07076  
5    20.31349  16.02301  11.652473  17.66347  19.88594  18.662840  12.07076  
..        ...       ...        ...       ...       ...        ...       ...  
964  20.67414  15.24188  11.652473  17.66347  18.98958  19.282875  12.07076  
965  20.26011  16.02301  11.652473  17.89835  19.47135  20.108640  12.07076  
966  20.51080  16.02301  11.652473  17.66347  19.30506  19.707450  12.65396  
967  20.90029  15.86242  11.232866  17.66347  19.44558  19.053560  11.89741  
968  20.51080  15.68142  11.652473  17.66347  19.32727  19.282875  11.94919  

[968 rows x 193 columns]

In [ ]:
DataTable_st2_med = DataTable_st2_med.dropna(subset=['Class'])
DataTable_st2_med.shape

(469, 193)

##Dealing with the noisy data

In [ ]:
DataTable.describe()

Idx       Class          M1          M2          M3          M4  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean   484.500000    0.501033   15.100309   14.588205   12.993140   11.916599   
std    279.581831    0.500257    0.287554    0.333544    1.187480    0.783079   
min      1.000000    0.000000   14.186670   13.273450    8.222473    6.885203   
25%    242.750000    0.000000   14.915625   14.358245   12.116768   11.428658   
50%    484.500000    1.000000   15.108960   14.581345   12.749361   11.966888   
75%    726.250000    1.000000   15.298583   14.807030   14.057987   12.426928   
max    968.000000    1.000000   15.994000   16.419860   16.143734   14.050150   

               M5          M6          M7          M8  ...        M180  \
count  968.000000  968.000000  968.000000  968.000000  ...  968.000000   
mean    11.538797   15.371513   17.197264   12.128846  ...   21.295237   
std      0.484311    0.408534    0.411065    0.688602  ...    0.529716   
min      8.545572   14.177460   14.913760    9.167940  ...   19.585810   
25%     11.275956   15.072188   16.942345   12.001918  ...   20.948845   
50%     11.574298   15.344485   17.207390   12.102878  ...   21.324510   
75%     11.846193   15.644862   17.470538   12.209416  ...   21.665195   
max     12.834166   17.036720   18.310400   18.341863  ...   22.564840   

             M181        M182        M183        M184        M185        M186  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean    20.569716   21.194328   20.433415   15.984485   11.636860   17.645289   
std      0.629455    0.421952    0.565416    0.537508    0.687066    0.420557   
min     18.461300   18.853580   17.375900   12.034610    8.916854   15.111250   
25%     20.132175   20.926545   20.067228   15.701028   11.210766   17.381912   
50%     20.550760   21.205055   20.469820   16.032305   11.657018   17.660590   
75%     21.015123   21.477598   20.841358   16.345013   12.113268   17.929012   
max     22.198270   22.527540   22.153810   17.930610   14.766459   19.114840   

             M187        M188        M189  
count  968.000000  968.000000  968.000000  
mean    19.275196   19.334282   12.030605  
std      0.483026    0.622501    0.492605  
min     14.980550   16.158640   10.034670  
25%     19.052482   18.920440   11.734338  
50%     19.337765   19.336895   12.068825  
75%     19.580535   19.752652   12.357138  
max     20.526510   21.080430   13.521310  

[8 rows x 191 columns]

In [ ]:
DataTable_st3.describe()

Idx       Class          M1          M2          M3          M4  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean   484.699111    0.305870   15.124957   14.754669   13.017792   11.952210   
std    279.540099    6.340726    5.674363    6.354180    6.230377    5.608657   
min     -4.767151  -40.267049  -34.708554  -34.861893  -50.525416  -44.648809   
25%    242.992221    0.000000   14.906568   14.336115   12.051935   11.390886   
50%    483.522068    0.000000   15.116590   14.587690   12.749361   11.968208   
75%    726.250000    1.000000   15.331122   14.851110   14.109359   12.497736   
max    970.681487   59.061028   53.301408   85.682926   58.593095   55.539272   

               M5          M6          M7          M8  ...        M180  \
count  968.000000  968.000000  968.000000  968.000000  ...  968.000000   
mean    11.610793   14.986551   17.100785   12.012603  ...   21.894686   
std      7.164939    6.618419    5.727931    5.904212  ...    7.426116   
min    -41.495462  -31.316082  -38.930103  -38.228821  ...  -52.278445   
25%     11.246112   15.042253   16.919153   11.981224  ...   20.904935   
50%     11.578000   15.335990   17.217195   12.100706  ...   21.322380   
75%     11.887884   15.661613   17.499353   12.224258  ...   21.716765   
max     78.464472   60.857947   58.593916   52.154737  ...   72.678992   

             M181        M182        M183        M184        M185        M186  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean    20.585788   21.498897   20.166881   16.318718   11.682875   17.756110   
std      5.887202    6.748596    6.022042    6.796626    6.767518    5.894492   
min    -25.314701  -30.162536  -24.464655  -43.327017  -34.153574  -28.512036   
25%     20.050287   20.895272   19.996235   15.684645   11.155656   17.358422   
50%     20.539240   21.204745   20.465865   16.054805   11.649798   17.664220   
75%     21.039265   21.519390   20.887590   16.404938   12.146379   17.963977   
max     66.163608   81.531359   83.690890   65.414553   66.185185   58.201783   

             M187        M188        M189  
count  968.000000  968.000000  968.000000  
mean    19.174794   19.309129   12.203615  
std      5.816586    6.272717    6.041990  
min    -22.614567  -37.342318  -36.003129  
25%     19.000685   18.879938   11.704733  
50%     19.336055   19.336895   12.065220  
75%     19.592115   19.819433   12.375013  
max     75.027493   69.189114   61.467603  

[8 rows x 191 columns]

There seems to be outliers in the data(just as intended). Q1, med and Q3 are very close in comparison to  max and min values in the dataset, which is also the reason behind why the mean of the data is still close to the original data, but an increase in the standard deviation.

In [ ]:
DataTable_st4.describe()

Idx       Class          M1          M2          M3  \
count   968.000000  968.000000  968.000000  968.000000  968.000000   
mean    484.707973    0.664607   14.676336   15.830295   13.931072   
std     279.568518   13.844443   15.651462   14.357155   14.254781   
min     -16.700120  -63.491540  -47.605499  -50.950322  -44.481975   
25%     244.750000    0.000000   13.102749   14.034655   11.549354   
50%     480.521112    0.000000   15.084920   14.632180   12.822948   
75%     727.078050    1.000000   15.774858   17.828092   15.037406   
max    1027.827269   59.324347   76.747546   87.385293   73.143237   

               M4          M5          M6          M7          M8  ...  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  ...   
mean    11.447528   11.220248   15.673659   18.025514   12.207974  ...   
std     14.703032   13.630966   14.597446   14.630068   14.149099  ...   
min    -56.373962  -55.282868  -42.617861  -37.929631  -45.788325  ...   
25%      9.597785   10.161022   14.489105   16.532050   11.692211  ...   
50%     11.936618   11.566036   15.375580   17.240510   12.097509  ...   
75%     13.149422   12.266463   16.706711   20.041197   13.819714  ...   
max     69.074824   62.165968   74.965420   72.446126   75.507967  ...   

             M180        M181        M182        M183        M184        M185  \
count  968.000000  968.000000  968.000000  968.000000  968.000000  968.000000   
mean    20.851385   20.577393   20.675129   20.109002   16.018280   11.877179   
std     13.831214   13.544246   13.498210   14.876370   13.950150   13.264628   
min    -44.150555  -41.830901  -32.916907  -46.744672  -34.862602  -38.460564   
25%     20.178263   19.568227   19.471585   18.685824   15.037000   10.440727   
50%     21.341675   20.582330   21.178620   20.418110   16.025885   11.668445   
75%     22.151305   21.659535   21.944871   21.323950   16.888683   12.751531   
max     73.919486   78.241633   79.152739   85.967421   74.305082   65.317954   

             M186        M187        M188        M189  
count  968.000000  968.000000  968.000000  968.000000  
mean    18.045808   19.469403   19.919045   12.388362  
std     14.789150   13.821529   14.167621   14.091986  
min    -67.189017  -37.489168  -57.519940  -53.314786  
25%     16.997547   18.371295   18.385185   11.241083  
50%     17.664705   19.384775   19.404555   12.111015  
75%     18.528683   20.981962   20.723004   12.914185  
max     88.542904   86.928102   78.691886   68.785291  

[8 rows x 191 columns]

The same analysis as before however there are even bigger outlier and more increase in the standard deviatio.

### Replace outliers using the median of the data.

In [ ]:
def replace_outliers_with_median(df): 
  for column in df.columns:
    df[column] = df[column].apply(lambda x: df.median()[column] 
                                  if x < (df.quantile(0.25)[column]-(1.5*(df.quantile(0.75)[column]-df.quantile(0.25)[column]))) 
                                  or x > (df.quantile(0.75)[column]+(1.5*(df.quantile(0.75)[column]-df.quantile(0.25)[column]))) 
                                  else x)
  return df

In [ ]:
test_df = pd.DataFrame({'Col1': [1, 2, 3, 4, 5, 600, 7, 8, 9],
                   'Col2': [10, 20, 30, 40, 500, 60, 70, 80, 90],
                   'Col3': [100, 200, 300, 400, 500, 600, 700, 800, 900],
                   'Col4': [10, 200, 30, 40, 500, 60, 70, 80, 90],
                   'Col5': [1, 2, 3, 4, 5, 600, 7, 8, 9]})

test_df.iloc[:,3:] = replace_outliers_with_median(df.iloc[:,3:])
test_df


<ipython-input-127-378c7887090a>:7: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  test_df.iloc[:,3:] = replace_outliers_with_median(df.iloc[:,3:])


Col1  Col2  Col3  Col4  Col5
0     1    10   100  10.0   1.0
1     2    20   200  70.0   2.0
2     3    30   300  30.0   3.0
3     4    40   400  40.0   4.0
4     5   500   500  70.0   5.0
5   600    60   600  60.0   5.0
6     7    70   700  70.0   7.0
7     8    80   800  80.0   8.0
8     9    90   900  90.0   9.0

#1. ML methods on Original Data


### 1(a) Extract X and Y

Dataframe = DataTable

In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable[(DataTable.Class == 1) | (DataTable.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                                     

###1(b) Hyperparameter Optimisation for PCR and Random Forest

In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 400/400 [00:43<00:00,  9.24it/s]


Time taken: 0.94 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 60/60 [10:45<00:00, 10.75s/it]


Time taken: 12.64 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)                                 

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2') 

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 110/110 [01:42<00:00,  1.07it/s]


Time taken: 1.79 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


###1(c) Build Models & Evaluate

In [ ]:
#1. pcr
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

###1(d) Bootstrap Evaluation

In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest)  

Number of cores set to: 2


100%|██████████| 100/100 [00:05<00:00, 19.44it/s]


Time taken: 0.09 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 

Number of cores set to: 2


100%|██████████| 100/100 [01:15<00:00,  1.33it/s]


Time taken: 1.32 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

###1.e Important features

In [ ]:
coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_1=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_1 

Idx  Name                                              Label  Importance
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.023684
142  142  M142                          Phosphatidylcholine(28:2)    0.023551
31    31   M31                     4-Hydroxy-3-methylbenzoic acid    0.023232
10    10   M10                                           Creatine    0.022261
93    93   M93                               m-Chlorobenzoic acid    0.021837
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.020841
80    80   M80                         2-(4-hydroxyphenyl)ethanol    0.020705
15    15   M15                                2-Ketohexanoic acid    0.019998
2      2    M2                                         Creatinine    0.019513
45    45   M45                    2,6 dimethylheptanoyl carnitine    0.018826

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_1=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_1 

Idx  Name                                              Label  Importance
10    10   M10                                           Creatine    0.105341
2      2    M2                                         Creatinine    0.092506
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.078281
142  142  M142                          Phosphatidylcholine(28:2)    0.077677
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.065498
18    18   M18                                          Uric acid    0.065214
15    15   M15                                2-Ketohexanoic acid    0.063428
28    28   M28                                  Indolelactic acid    0.060485
7      7    M7                                            Betaine    0.057364
24    24   M24                           1,3,7-Trimethyluric acid    0.057248

In [ ]:
common_imp_var_1 = pd.merge(svm_imp10_1, pcr_imp10_1, on='Name', how='inner') #common in both
common_imp_var_1


Idx_x  Name                                            Label_x  \
0     10   M10                                           Creatine   
1      2    M2                                         Creatinine   
2    141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...   
3    142  M142                          Phosphatidylcholine(28:2)   
4    152  M152                          Sphingomyelin(d18:2/18:1)   
5     15   M15                                2-Ketohexanoic acid   

   Importance_x  Idx_y                                            Label_y  \
0      0.105341     10                                           Creatine   
1      0.092506      2                                         Creatinine   
2      0.078281    141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...   
3      0.077677    142                          Phosphatidylcholine(28:2)   
4      0.065498    152                          Sphingomyelin(d18:2/18:1)   
5      0.063428     15                                2-Ketohexanoic acid   

   Importance_y  
0      0.022261  
1      0.019513  
2      0.023684  
3      0.023551  
4      0.020841  
5      0.019998

In [ ]:
common_imp_var_1 = common_imp_var.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_1[['Name','Label','SVM coef_ Score','PCR coef_ Score']])

   Name                                              Label  SVM coef_ Score  \
0   M10                                           Creatine         0.105341   
1    M2                                         Creatinine         0.092506   
2  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...         0.078281   
3  M142                          Phosphatidylcholine(28:2)         0.077677   
4  M152                          Sphingomyelin(d18:2/18:1)         0.065498   
5   M15                                2-Ketohexanoic acid         0.063428   

   PCR coef_ Score  
0         0.022261  
1         0.019513  
2         0.023684  
3         0.023551  
4         0.020841  
5         0.019998  


#2. ML methods on dataset with 10% data points removed

Dataframe = DataTable_st1


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st1[(DataTable_st1.Class == 1) | (DataTable_st1.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                                     

ValueError: ignored

knnimpute method from cimcb library is sensitive to NaN values. It was commented for further analysis

In [ ]:
#-------knnimpute lines are commented-------
#-------------------------------------------

# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st1[(DataTable_st1.Class == 1) | (DataTable_st1.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
#XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
#XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                                     

In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainScale,    #from XTranKnn changed to XTrainScale                             
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...






1/2:   0%|          | 0/40 [00:00<?, ?it/s]



1/2:   5%|▌         | 2/40 [00:00<00:05,  6.58it/s]



1/2:  10%|█         | 4/40 [00:11<02:00,  3.34s/it]

TerminatedWorkerError was raised due to excessive memory usage. n_cores was reduced to 1.







1/2:   0%|          | 0/40 [00:00<?, ?it/s]

ValueError: ignored

PCR is sensitive to NaN

In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainScale,       #changed to scaled trained data                          
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...








1/2:   0%|          | 0/6 [00:00<?, ?it/s]





1/2:  33%|███▎      | 2/6 [00:00<00:00,  5.90it/s]





1/2:  67%|██████▋   | 4/6 [00:12<00:07,  3.65s/it]





1/2: 100%|██████████| 6/6 [00:12<00:00,  2.12s/it]


TerminatedWorkerError was raised due to excessive memory usage. n_cores was reduced to 1.








1/2:   0%|          | 0/6 [00:00<?, ?it/s]

ValueError: ignored

SVM is also sensitive to NaN

We get an error the first time because knnimpute method is sensitive to NaN values. The next time knnimpute part was commented but again an error was thrown by both the PCA and the SVM algorithms because of the presence of NaN.

This cannot be solved since as observed earlier, every row in the dataset has at least one NaN value, therefore dropping na will be useless as no data will be left in the dataframe. 

#3. ML methods on dataset with 50% data points removed

Dataframe = DataTable_st2


We will get the same errors as above(2) because in DataTable_st2 data as well, every row had at least one NaN. Thus, we did not try to run the code for the dataframe.

#4. Dataset - 10% data removed, imputation method - Mean

Dataframe - DataTable_st1_mean


###4(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st1_mean[(DataTable_st1_mean.Class == 1) | (DataTable_st1_mean.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                           


###4(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...











1/2:   0%|          | 0/40 [00:00<?, ?it/s]








1/2:   5%|▌         | 2/40 [00:00<00:02, 17.78it/s]








1/2:  10%|█         | 4/40 [00:08<01:30,  2.51s/it]








1/2:  15%|█▌        | 6/40 [00:08<00:49,  1.45s/it]








1/2:  30%|███       | 12/40 [00:09<00:14,  1.98it/s]








1/2:  45%|████▌     | 18/40 [00:09<00:05,  3.72it/s]








1/2:  60%|██████    | 24/40 [00:09<00:02,  6.03it/s]








1/2: 100%|██████████| 40/40 [00:09<00:00,  4.23it/s]









2/2:   0%|          | 0/400 [00:00<?, ?it/s]








2/2:   1%|          | 4/400 [00:00<00:28, 14.02it/s]








2/2:   2%|▏         | 6/400 [00:00<00:41,  9.44it/s]








2/2:   2%|▏         | 8/400 [00:00<00:43,  8.97it/s]








2/2:   2%|▎         | 10/400 [00:01<00:44,  8.81it/s]








2/2:   3%|▎         | 12/400 [00:01<00:46,  8.35it/s]








2/2:   4%|▎         | 14/400 [00:01<00:49,  7.86it/s]








2/2:   4%|▍         | 16/400 [00:01<00:51,  7.53it/s]








2/2:   4%|▍         | 18/400 [

Time taken: 1.26 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:

#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...











1/2:   0%|          | 0/6 [00:00<?, ?it/s]








1/2:  67%|██████▋   | 4/6 [00:09<00:04,  2.49s/it]








1/2: 100%|██████████| 6/6 [00:10<00:00,  1.77s/it]









2/2:   0%|          | 0/60 [00:00<?, ?it/s]








2/2:   7%|▋         | 4/60 [00:01<00:19,  2.92it/s]








2/2:  10%|█         | 6/60 [00:02<00:22,  2.38it/s]








2/2:  13%|█▎        | 8/60 [00:10<01:31,  1.77s/it]








2/2:  17%|█▋        | 10/60 [00:13<01:20,  1.60s/it]








2/2:  20%|██        | 12/60 [00:15<01:11,  1.50s/it]








2/2:  23%|██▎       | 14/60 [00:23<01:45,  2.29s/it]








2/2:  27%|██▋       | 16/60 [00:26<01:28,  2.01s/it]








2/2:  30%|███       | 18/60 [00:28<01:15,  1.79s/it]








2/2:  33%|███▎      | 20/60 [00:34<01:22,  2.06s/it]








2/2:  37%|███▋      | 22/60 [00:38<01:20,  2.12s/it]








2/2:  40%|████      | 24/60 [00:42<01:10,  1.96s/it]








2/2:  43%|████▎     | 26/60 [00:47<01:14,  2.18s/it]








2/2:  47%|████▋     | 28/60 [00:49<01:00

Time taken: 2.59 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)                                 

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2') 



Number of cores set to: 2
Running ...











1/2:   0%|          | 0/11 [00:00<?, ?it/s]








1/2:  36%|███▋      | 4/11 [00:00<00:00,  8.45it/s]








1/2:  55%|█████▍    | 6/11 [00:01<00:01,  4.12it/s]








1/2:  73%|███████▎  | 8/11 [00:02<00:01,  2.58it/s]








1/2: 100%|██████████| 11/11 [00:04<00:00,  2.67it/s]









2/2:   0%|          | 0/110 [00:00<?, ?it/s]








2/2:   4%|▎         | 4/110 [00:02<00:57,  1.86it/s]








2/2:   5%|▌         | 6/110 [00:03<01:04,  1.61it/s]








2/2:   7%|▋         | 8/110 [00:05<01:05,  1.55it/s]








2/2:   9%|▉         | 10/110 [00:06<01:03,  1.58it/s]








2/2:  11%|█         | 12/110 [00:07<00:59,  1.63it/s]








2/2:  13%|█▎        | 14/110 [00:08<00:57,  1.68it/s]








2/2:  15%|█▍        | 16/110 [00:10<01:01,  1.52it/s]








2/2:  16%|█▋        | 18/110 [00:11<01:03,  1.46it/s]








2/2:  18%|█▊        | 20/110 [00:13<01:11,  1.27it/s]








2/2:  20%|██        | 22/110 [00:16<01:33,  1.06s/it]








2/2:  22%|██▏       | 24/11

Time taken: 1.90 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


###4(c) Build Models & Evaluate


In [ ]:
#1. pcr
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 


/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 


/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

###4(d) Bootstrap Evaluation


In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest)  


Number of cores set to: 2











  0%|          | 0/100 [00:00<?, ?it/s]








  8%|▊         | 8/100 [00:00<00:01, 54.47it/s]








 14%|█▍        | 14/100 [00:00<00:01, 48.68it/s]








 19%|█▉        | 19/100 [00:00<00:01, 44.83it/s]








 24%|██▍       | 24/100 [00:00<00:02, 30.61it/s]








 28%|██▊       | 28/100 [00:00<00:02, 31.47it/s]








 32%|███▏      | 32/100 [00:00<00:02, 30.68it/s]








 36%|███▌      | 36/100 [00:01<00:02, 29.99it/s]








 40%|████      | 40/100 [00:01<00:01, 30.69it/s]








 44%|████▍     | 44/100 [00:01<00:01, 28.41it/s]








 48%|████▊     | 48/100 [00:01<00:01, 29.38it/s]








 52%|█████▏    | 52/100 [00:01<00:01, 29.60it/s]








 56%|█████▌    | 56/100 [00:01<00:01, 29.35it/s]








 60%|██████    | 60/100 [00:01<00:01, 29.64it/s]








 64%|██████▍   | 64/100 [00:02<00:01, 27.95it/s]








 68%|██████▊   | 68/100 [00:02<00:01, 27.55it/s]








 72%|███████▏  | 72/100 [00:02<00:01, 25.97it/s]








 76%|███████▌  | 76/100 [00:02<0

Time taken: 0.06 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 


Number of cores set to: 2











  0%|          | 0/100 [00:00<?, ?it/s]








  4%|▍         | 4/100 [00:01<00:29,  3.20it/s]








  6%|▌         | 6/100 [00:02<00:46,  2.04it/s]








  8%|▊         | 8/100 [00:04<00:52,  1.77it/s]








 10%|█         | 10/100 [00:05<00:57,  1.57it/s]








 12%|█▏        | 12/100 [00:06<00:51,  1.71it/s]








 14%|█▍        | 14/100 [00:07<00:45,  1.89it/s]








 16%|█▌        | 16/100 [00:08<00:41,  2.02it/s]








 18%|█▊        | 18/100 [00:09<00:39,  2.09it/s]








 20%|██        | 20/100 [00:10<00:38,  2.10it/s]








 22%|██▏       | 22/100 [00:11<00:37,  2.10it/s]








 24%|██▍       | 24/100 [00:12<00:36,  2.11it/s]








 26%|██▌       | 26/100 [00:13<00:36,  2.05it/s]








 28%|██▊       | 28/100 [00:14<00:36,  1.97it/s]








 30%|███       | 30/100 [00:15<00:36,  1.90it/s]








 32%|███▏      | 32/100 [00:16<00:39,  1.71it/s]








 34%|███▍      | 34/100 [00:18<00:49,  1.34it/s]








 36%|███▌      | 36/100 [00:21<00:

Time taken: 1.41 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

###4(e) Important features


In [ ]:

coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_4=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_4 


Idx  Name                                              Label  Importance
15    15   M15                                2-Ketohexanoic acid    0.024884
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.024578
142  142  M142                          Phosphatidylcholine(28:2)    0.024166
10    10   M10                                           Creatine    0.023450
2      2    M2                                         Creatinine    0.022566
28    28   M28                                  Indolelactic acid    0.021378
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.020935
4      4    M4                            DL-2-Aminooctanoic acid    0.020134
11    11   M11                             L-Leucine|L-Norleucine    0.019956
7      7    M7                                            Betaine    0.019876

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_4=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_4 

Idx  Name                                              Label  Importance
10    10   M10                                           Creatine    0.103244
2      2    M2                                         Creatinine    0.082617
142  142  M142                          Phosphatidylcholine(28:2)    0.076085
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.066208
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.066004
18    18   M18                                          Uric acid    0.063106
15    15   M15                                2-Ketohexanoic acid    0.063040
24    24   M24                           1,3,7-Trimethyluric acid    0.062257
7      7    M7                                            Betaine    0.056336
148  148  M148                          Phosphatidylcholine(30:2)    0.053127

In [ ]:
common_imp_var_4 = pd.merge(svm_imp10_4, pcr_imp10_4, on='Name', how='inner') #common in both
common_imp_var_4 = common_imp_var_4.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_4[['Name','Label','SVM coef_ Score','PCR coef_ Score']])

   Name                                              Label  SVM coef_ Score  \
0   M10                                           Creatine         0.103244   
1    M2                                         Creatinine         0.082617   
2  M142                          Phosphatidylcholine(28:2)         0.076085   
3  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...         0.066208   
4  M152                          Sphingomyelin(d18:2/18:1)         0.066004   
5   M15                                2-Ketohexanoic acid         0.063040   
6    M7                                            Betaine         0.056336   

   PCR coef_ Score  
0         0.023450  
1         0.022566  
2         0.024166  
3         0.024578  
4         0.020935  
5         0.024884  
6         0.019876  


#5. Dataset - 10% data removed, imputation method - Median

Dataset = DataTable_st1_med

###5(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st1_med[(DataTable_st1_med.Class == 1) | (DataTable_st1_med.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                           


###5(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:

#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...











1/2:   0%|          | 0/40 [00:00<?, ?it/s]








1/2:   5%|▌         | 2/40 [00:00<00:02, 18.44it/s]








1/2:  10%|█         | 4/40 [00:07<01:17,  2.15s/it]








1/2:  15%|█▌        | 6/40 [00:07<00:44,  1.29s/it]








1/2:  25%|██▌       | 10/40 [00:08<00:17,  1.73it/s]








1/2:  35%|███▌      | 14/40 [00:08<00:08,  3.00it/s]








1/2:  45%|████▌     | 18/40 [00:08<00:04,  4.60it/s]








1/2:  55%|█████▌    | 22/40 [00:08<00:02,  6.58it/s]








1/2:  65%|██████▌   | 26/40 [00:08<00:01,  8.84it/s]








1/2:  80%|████████  | 32/40 [00:08<00:00, 13.51it/s]








1/2: 100%|██████████| 40/40 [00:08<00:00,  4.54it/s]









2/2:   0%|          | 0/400 [00:00<?, ?it/s]








2/2:   1%|          | 4/400 [00:00<00:39,  9.95it/s]








2/2:   2%|▏         | 6/400 [00:00<00:54,  7.29it/s]








2/2:   2%|▏         | 8/400 [00:01<01:11,  5.48it/s]








2/2:   2%|▎         | 10/400 [00:01<01:32,  4.24it/s]








2/2:   3%|▎         | 12/400 [00:

Time taken: 1.51 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...











1/2:   0%|          | 0/6 [00:00<?, ?it/s]








1/2:  67%|██████▋   | 4/6 [00:00<00:00, 11.08it/s]








1/2: 100%|██████████| 6/6 [00:00<00:00,  8.65it/s]









2/2:   0%|          | 0/60 [00:00<?, ?it/s]








2/2:   7%|▋         | 4/60 [00:03<00:49,  1.13it/s]








2/2:  10%|█         | 6/60 [00:05<00:45,  1.19it/s]








2/2:  13%|█▎        | 8/60 [00:13<01:45,  2.03s/it]








2/2:  17%|█▋        | 10/60 [00:17<01:41,  2.04s/it]








2/2:  20%|██        | 12/60 [00:20<01:34,  1.97s/it]








2/2:  23%|██▎       | 14/60 [00:26<01:43,  2.26s/it]








2/2:  27%|██▋       | 16/60 [00:29<01:28,  2.01s/it]








2/2:  30%|███       | 18/60 [00:36<01:39,  2.38s/it]








2/2:  33%|███▎      | 20/60 [00:43<01:49,  2.74s/it]








2/2:  37%|███▋      | 22/60 [00:47<01:37,  2.56s/it]








2/2:  40%|████      | 24/60 [00:53<01:36,  2.69s/it]








2/2:  43%|████▎     | 26/60 [01:07<02:15,  4.00s/it]








2/2:  47%|████▋     | 28/60 [01:12<01:53

Time taken: 3.48 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10) 
# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2')

Number of cores set to: 2
Running ...











1/2:   0%|          | 0/11 [00:00<?, ?it/s]








1/2:  36%|███▋      | 4/11 [00:00<00:00,  9.13it/s]








1/2:  55%|█████▍    | 6/11 [00:00<00:00,  6.81it/s]








1/2:  73%|███████▎  | 8/11 [00:01<00:00,  6.12it/s]








1/2: 100%|██████████| 11/11 [00:01<00:00,  7.13it/s]









2/2:   0%|          | 0/110 [00:00<?, ?it/s]








2/2:   4%|▎         | 4/110 [00:01<00:41,  2.56it/s]








2/2:   5%|▌         | 6/110 [00:03<00:55,  1.87it/s]








2/2:   7%|▋         | 8/110 [00:04<00:59,  1.70it/s]








2/2:   9%|▉         | 10/110 [00:05<00:59,  1.69it/s]








2/2:  11%|█         | 12/110 [00:06<00:56,  1.73it/s]








2/2:  13%|█▎        | 14/110 [00:08<01:02,  1.54it/s]








2/2:  15%|█▍        | 16/110 [00:10<01:19,  1.18it/s]








2/2:  16%|█▋        | 18/110 [00:12<01:23,  1.10it/s]








2/2:  18%|█▊        | 20/110 [00:14<01:15,  1.19it/s]








2/2:  20%|██        | 22/110 [00:15<01:06,  1.32it/s]








2/2:  22%|██▏       | 24/11

Time taken: 1.45 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


###1(c) Build Models & Evaluate




In [ ]:
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

###5(d) Bootstrap Evaluation


In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest)  


Number of cores set to: 2











  0%|          | 0/100 [00:00<?, ?it/s]








  8%|▊         | 8/100 [00:00<00:01, 51.22it/s]








 14%|█▍        | 14/100 [00:00<00:01, 48.30it/s]








 20%|██        | 20/100 [00:00<00:01, 47.37it/s]








 28%|██▊       | 28/100 [00:00<00:01, 42.01it/s]








 36%|███▌      | 36/100 [00:00<00:01, 40.37it/s]








 44%|████▍     | 44/100 [00:01<00:01, 39.82it/s]








 52%|█████▏    | 52/100 [00:01<00:01, 37.89it/s]








 60%|██████    | 60/100 [00:01<00:01, 36.52it/s]








 68%|██████▊   | 68/100 [00:01<00:00, 36.52it/s]








 76%|███████▌  | 76/100 [00:01<00:00, 36.30it/s]








 84%|████████▍ | 84/100 [00:02<00:00, 36.74it/s]








 92%|█████████▏| 92/100 [00:02<00:00, 36.74it/s]








100%|██████████| 100/100 [00:02<00:00, 38.60it/s]


Time taken: 0.05 minutes with 2 cores


1/2:   0%|          | 0/6 [56:34<?, ?it/s]
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pan

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 



Number of cores set to: 2








  0%|          | 0/100 [00:00<?, ?it/s]





  4%|▍         | 4/100 [00:01<00:30,  3.16it/s]





  6%|▌         | 6/100 [00:02<00:47,  2.00it/s]





  8%|▊         | 8/100 [00:04<00:52,  1.74it/s]





 10%|█         | 10/100 [00:05<00:57,  1.57it/s]





 12%|█▏        | 12/100 [00:06<00:50,  1.75it/s]





 14%|█▍        | 14/100 [00:07<00:46,  1.86it/s]





 16%|█▌        | 16/100 [00:08<00:43,  1.95it/s]





 18%|█▊        | 18/100 [00:09<00:40,  2.04it/s]





 20%|██        | 20/100 [00:10<00:38,  2.09it/s]





 22%|██▏       | 22/100 [00:11<00:35,  2.17it/s]





 24%|██▍       | 24/100 [00:11<00:34,  2.22it/s]





 26%|██▌       | 26/100 [00:12<00:33,  2.24it/s]





 28%|██▊       | 28/100 [00:13<00:32,  2.24it/s]





 30%|███       | 30/100 [00:14<00:31,  2.23it/s]





 32%|███▏      | 32/100 [00:15<00:30,  2.24it/s]





 34%|███▍      | 34/100 [00:16<00:31,  2.08it/s]





 36%|███▌      | 36/100 [00:18<00:35,  1.79it/s]





 38%|███▊      | 38/100 [00:19<00:

Time taken: 0.89 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

###5(e) Important features


In [ ]:
coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_5=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_5 

Idx  Name                                              Label  Importance
15    15   M15                                2-Ketohexanoic acid    0.024344
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.024206
142  142  M142                          Phosphatidylcholine(28:2)    0.023768
10    10   M10                                           Creatine    0.022964
2      2    M2                                         Creatinine    0.022158
28    28   M28                                  Indolelactic acid    0.020887
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.020674
7      7    M7                                            Betaine    0.020027
4      4    M4                            DL-2-Aminooctanoic acid    0.019981
35    35   M35                             gamma-Glutamyl-leucine    0.019539

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_5=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_5 


Idx  Name                                              Label  Importance
10    10   M10                                           Creatine    0.103704
2      2    M2                                         Creatinine    0.081823
142  142  M142                          Phosphatidylcholine(28:2)    0.076303
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.066216
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.065857
15    15   M15                                2-Ketohexanoic acid    0.063062
18    18   M18                                          Uric acid    0.062397
24    24   M24                           1,3,7-Trimethyluric acid    0.061481
7      7    M7                                            Betaine    0.057055
148  148  M148                          Phosphatidylcholine(30:2)    0.053031

In [ ]:

common_imp_var_5 = pd.merge(svm_imp10_5, pcr_imp10_5, on='Name', how='inner') #common in both
common_imp_var_5 = common_imp_var_5.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_5[['Name','Label','SVM coef_ Score','PCR coef_ Score']])

   Name                                              Label  SVM coef_ Score  \
0   M10                                           Creatine         0.103704   
1    M2                                         Creatinine         0.081823   
2  M142                          Phosphatidylcholine(28:2)         0.076303   
3  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...         0.066216   
4  M152                          Sphingomyelin(d18:2/18:1)         0.065857   
5   M15                                2-Ketohexanoic acid         0.063062   
6    M7                                            Betaine         0.057055   

   PCR coef_ Score  
0         0.022964  
1         0.022158  
2         0.023768  
3         0.024206  
4         0.020674  
5         0.024344  
6         0.020027  


#6. Dataset - 10% data removed, imputation method - Remove all rows with null

In [ ]:
DataTable_st1_NaN_rm = DataTable_st1.dropna()
DataTable_st1_NaN_rm

Empty DataFrame
Columns: [Idx, SampleID, Class, Sex, M1, M2, M3, M4, M5, M6, M7, M8, M9, M10, M11, M12, M13, M14, M15, M16, M17, M18, M19, M20, M21, M22, M23, M24, M25, M26, M27, M28, M29, M30, M31, M32, M33, M34, M35, M36, M37, M38, M39, M40, M41, M42, M43, M44, M45, M46, M47, M48, M49, M50, M51, M52, M53, M54, M55, M56, M57, M58, M59, M60, M61, M62, M63, M64, M65, M66, M67, M68, M69, M70, M71, M72, M73, M74, M75, M76, M77, M78, M79, M80, M81, M82, M83, M84, M85, M86, M87, M88, M89, M90, M91, M92, M93, M94, M95, M96, ...]
Index: []

[0 rows x 193 columns]

As discussed earlier as well, there will be no dataset left if all rows with NaN are removed. This is because after changing 10% of data to be NaN, coincidentally every row got at least one NaN.

#7. Dataset - 50% data removed, imputation method - Mean

dataframe - DataTable_st2_mean

###7(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st2_mean[(DataTable_st2_mean.Class == 1) | (DataTable_st2_mean.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                           



###7(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')


Number of cores set to: 2
Running ...








1/2:   0%|          | 0/40 [00:00<?, ?it/s]





1/2:   5%|▌         | 2/40 [00:00<00:01, 19.69it/s]





1/2:   5%|▌         | 2/40 [00:11<00:01, 19.69it/s]





1/2:  10%|█         | 4/40 [00:11<01:58,  3.30s/it]





1/2:  15%|█▌        | 6/40 [00:11<01:05,  1.92s/it]





1/2:  20%|██        | 8/40 [00:11<00:38,  1.19s/it]





1/2:  25%|██▌       | 10/40 [00:12<00:23,  1.26it/s]





1/2:  35%|███▌      | 14/40 [00:12<00:10,  2.44it/s]





1/2:  45%|████▌     | 18/40 [00:12<00:05,  3.93it/s]





1/2:  55%|█████▌    | 22/40 [00:12<00:03,  5.79it/s]





1/2:  65%|██████▌   | 26/40 [00:12<00:01,  8.24it/s]





1/2:  75%|███████▌  | 30/40 [00:12<00:00, 10.85it/s]





1/2: 100%|██████████| 40/40 [00:13<00:00,  3.07it/s]






2/2:   0%|          | 0/400 [00:00<?, ?it/s]





2/2:   1%|          | 4/400 [00:00<00:26, 14.68it/s]





2/2:   2%|▏         | 6/400 [00:00<00:39,  9.95it/s]





2/2:   2%|▏         | 8/400 [00:00<00:50,  7.69it/s]





2/2:   2%|▎         | 10/400 

Time taken: 1.32 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)  

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...








1/2:   0%|          | 0/6 [00:00<?, ?it/s]





1/2: 100%|██████████| 6/6 [00:00<00:00, 47.75it/s]






2/2:   0%|          | 0/60 [00:00<?, ?it/s]





2/2:   7%|▋         | 4/60 [00:00<00:06,  8.80it/s]





2/2:  10%|█         | 6/60 [00:00<00:09,  5.61it/s]





2/2:  13%|█▎        | 8/60 [00:01<00:13,  3.82it/s]





2/2:  17%|█▋        | 10/60 [00:02<00:16,  3.06it/s]





2/2:  20%|██        | 12/60 [00:03<00:16,  2.88it/s]





2/2:  23%|██▎       | 14/60 [00:04<00:18,  2.54it/s]





2/2:  27%|██▋       | 16/60 [00:05<00:17,  2.45it/s]





2/2:  30%|███       | 18/60 [00:06<00:16,  2.47it/s]





2/2:  33%|███▎      | 20/60 [00:06<00:14,  2.76it/s]





2/2:  37%|███▋      | 22/60 [00:07<00:12,  3.13it/s]





2/2:  40%|████      | 24/60 [00:07<00:10,  3.52it/s]





2/2:  43%|████▎     | 26/60 [00:08<00:09,  3.65it/s]





2/2:  47%|████▋     | 28/60 [00:08<00:08,  3.84it/s]





2/2:  50%|█████     | 30/60 [00:08<00:07,  4.12it/s]





2/2:  53%|█████▎    | 32/60 [00

Time taken: 0.30 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():
2/2:  20%|██        | 82/400 [1:13:08<4:43:39, 53.52s/it]


In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)                                 

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2') 

Number of cores set to: 2
Running ...








1/2:   0%|          | 0/11 [00:00<?, ?it/s]





1/2:  36%|███▋      | 4/11 [00:00<00:00, 31.91it/s]





1/2: 100%|██████████| 11/11 [00:00<00:00, 41.55it/s]






2/2:   0%|          | 0/110 [00:00<?, ?it/s]





2/2:   4%|▎         | 4/110 [00:00<00:12,  8.50it/s]





2/2:   5%|▌         | 6/110 [00:00<00:16,  6.12it/s]





2/2:   7%|▋         | 8/110 [00:01<00:19,  5.36it/s]





2/2:   9%|▉         | 10/110 [00:01<00:19,  5.10it/s]





2/2:  11%|█         | 12/110 [00:02<00:19,  5.15it/s]





2/2:  13%|█▎        | 14/110 [00:02<00:18,  5.10it/s]





2/2:  15%|█▍        | 16/110 [00:03<00:19,  4.82it/s]





2/2:  16%|█▋        | 18/110 [00:03<00:20,  4.56it/s]





2/2:  18%|█▊        | 20/110 [00:04<00:20,  4.45it/s]





2/2:  20%|██        | 22/110 [00:04<00:19,  4.58it/s]





2/2:  22%|██▏       | 24/110 [00:04<00:18,  4.76it/s]





2/2:  24%|██▎       | 26/110 [00:05<00:19,  4.39it/s]





2/2:  25%|██▌       | 28/110 [00:06<00:22,  3.61it/s]





2/2:  27%|██▋  

Time taken: 0.50 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


###7(c) Build Models & Evaluate


In [ ]:
#1. pcr
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [ ]:
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

###7(d) Bootstrap Evaluation


In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest)  

Number of cores set to: 2








  0%|          | 0/100 [00:00<?, ?it/s]





  8%|▊         | 8/100 [00:00<00:01, 49.45it/s]





 13%|█▎        | 13/100 [00:00<00:02, 40.74it/s]





 18%|█▊        | 18/100 [00:00<00:02, 36.50it/s]





 22%|██▏       | 22/100 [00:00<00:02, 35.92it/s]





 26%|██▌       | 26/100 [00:00<00:02, 33.39it/s]





 30%|███       | 30/100 [00:00<00:02, 26.39it/s]





 33%|███▎      | 33/100 [00:01<00:02, 23.30it/s]





 36%|███▌      | 36/100 [00:01<00:03, 18.37it/s]





 40%|████      | 40/100 [00:01<00:03, 17.78it/s]





 44%|████▍     | 44/100 [00:01<00:03, 17.20it/s]





 48%|████▊     | 48/100 [00:02<00:03, 16.33it/s]





 52%|█████▏    | 52/100 [00:02<00:02, 16.01it/s]





 56%|█████▌    | 56/100 [00:02<00:02, 16.19it/s]





 60%|██████    | 60/100 [00:02<00:02, 16.15it/s]





 64%|██████▍   | 64/100 [00:03<00:02, 16.10it/s]





 68%|██████▊   | 68/100 [00:03<00:01, 16.00it/s]





 72%|███████▏  | 72/100 [00:03<00:01, 17.87it/s]





 76%|███████▌  | 76/100 [00:03<0

Time taken: 0.09 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 

Number of cores set to: 2








  0%|          | 0/100 [00:00<?, ?it/s]





  4%|▍         | 4/100 [00:00<00:06, 14.16it/s]





  6%|▌         | 6/100 [00:00<00:09,  9.88it/s]





  8%|▊         | 8/100 [00:00<00:10,  8.51it/s]





 10%|█         | 10/100 [00:01<00:11,  7.88it/s]





 12%|█▏        | 12/100 [00:01<00:11,  7.56it/s]





 14%|█▍        | 14/100 [00:01<00:11,  7.24it/s]





 16%|█▌        | 16/100 [00:02<00:11,  7.04it/s]





 18%|█▊        | 18/100 [00:02<00:11,  6.92it/s]





 20%|██        | 20/100 [00:02<00:11,  6.91it/s]





 22%|██▏       | 22/100 [00:02<00:11,  6.91it/s]





 24%|██▍       | 24/100 [00:03<00:11,  6.81it/s]





 26%|██▌       | 26/100 [00:03<00:10,  6.80it/s]





 28%|██▊       | 28/100 [00:03<00:10,  6.84it/s]





 30%|███       | 30/100 [00:04<00:10,  6.90it/s]





 32%|███▏      | 32/100 [00:04<00:09,  6.94it/s]





 34%|███▍      | 34/100 [00:04<00:09,  6.85it/s]





 36%|███▌      | 36/100 [00:04<00:09,  6.72it/s]





 38%|███▊      | 38/100 [00:05<00:

Time taken: 0.29 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

###7(e) Important features


In [ ]:

coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_7=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_7 

Idx  Name                                              Label  Importance
142  142  M142                          Phosphatidylcholine(28:2)    0.031132
28    28   M28                                  Indolelactic acid    0.030830
2      2    M2                                         Creatinine    0.026835
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.024608
146  146  M146                                          Ornithine    0.024293
11    11   M11                             L-Leucine|L-Norleucine    0.023946
35    35   M35                             gamma-Glutamyl-leucine    0.023548
15    15   M15                                2-Ketohexanoic acid    0.023164
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.022705
18    18   M18                                          Uric acid    0.021611

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_7=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_7 

Idx  Name                                              Label  Importance
142  142  M142                          Phosphatidylcholine(28:2)    0.059196
10    10   M10                                           Creatine    0.057232
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.049490
2      2    M2                                         Creatinine    0.048834
152  152  M152                          Sphingomyelin(d18:2/18:1)    0.046401
18    18   M18                                          Uric acid    0.044801
4      4    M4                            DL-2-Aminooctanoic acid    0.044255
6      6    M6                                          L-Proline    0.042638
7      7    M7                                            Betaine    0.042079
28    28   M28                                  Indolelactic acid    0.040626

In [ ]:
common_imp_var_7 = pd.merge(svm_imp10_7, pcr_imp10_7, on='Name', how='inner') #common in both
common_imp_var_7 = common_imp_var_7.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_7[['Name','Label','SVM coef_ Score','PCR coef_ Score']])



   Name                                              Label  SVM coef_ Score  \
0  M142                          Phosphatidylcholine(28:2)         0.059196   
1  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...         0.049490   
2    M2                                         Creatinine         0.048834   
3  M152                          Sphingomyelin(d18:2/18:1)         0.046401   
4   M18                                          Uric acid         0.044801   
5   M28                                  Indolelactic acid         0.040626   

   PCR coef_ Score  
0         0.031132  
1         0.024608  
2         0.026835  
3         0.022705  
4         0.021611  
5         0.030830  


#8 ML methods on dataset with 50% data removed, imputation method - Median

dataframe = DataTable_st2_med


###8(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st2_med[(DataTable_st2_med.Class == 1) | (DataTable_st2_med.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                           


###8(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 400/400 [01:01<00:00,  6.53it/s]


Time taken: 1.37 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 60/60 [00:20<00:00,  2.87it/s]


Time taken: 0.39 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)                                 

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2') 

Number of cores set to: 2
Running ...


2/2: 100%|██████████| 110/110 [00:39<00:00,  2.81it/s]


Time taken: 0.68 minutes with 2 cores
Done!


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:562: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in full_std.iteritems():
/usr/local/lib/python3.10/dist-packages/cimcb/cross_val/BaseCrossVal.py:567: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for key, values in cv_std.iteritems():


###8(c) Build Models & Evaluate


In [ ]:
#1. pcr
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:367: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:368: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/model/BaseModel.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

###8(d) Bootstrap Evaluation


In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)


In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest)  


Number of cores set to: 2


100%|██████████| 100/100 [00:06<00:00, 15.69it/s]


Time taken: 0.11 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 



Number of cores set to: 2


100%|██████████| 100/100 [00:21<00:00,  4.58it/s]


Time taken: 0.39 minutes with 2 cores


/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:343: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][0] = np.round(self.table[i][0], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:344: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.table[i][1] = np.round(self.table[i][1], 2)
/usr/local/lib/python3.10/dist-packages/cimcb/bootstrap/BaseBootstrap.py:348: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

###8(e) Important features


In [ ]:
coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_8=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_8 

Idx  Name                                              Label  Importance
35    35   M35                             gamma-Glutamyl-leucine    0.029296
10    10   M10                                           Creatine    0.028100
142  142  M142                          Phosphatidylcholine(28:2)    0.025117
4      4    M4                            DL-2-Aminooctanoic acid    0.023038
24    24   M24                           1,3,7-Trimethyluric acid    0.022954
11    11   M11                             L-Leucine|L-Norleucine    0.022664
2      2    M2                                         Creatinine    0.021007
147  147  M147  Ceramide phosphoethanolamine(37:2)|Sphingomyel...    0.020677
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.020239
148  148  M148                          Phosphatidylcholine(30:2)    0.020178

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_8=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_8 

Idx  Name                                              Label  Importance
10    10   M10                                           Creatine    0.069388
2      2    M2                                         Creatinine    0.058710
35    35   M35                             gamma-Glutamyl-leucine    0.056520
142  142  M142                          Phosphatidylcholine(28:2)    0.056014
141  141  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...    0.053308
7      7    M7                                            Betaine    0.050469
11    11   M11                             L-Leucine|L-Norleucine    0.047938
28    28   M28                                  Indolelactic acid    0.047565
24    24   M24                           1,3,7-Trimethyluric acid    0.045943
18    18   M18                                          Uric acid    0.043171

In [ ]:
common_imp_var_8 = pd.merge(svm_imp10_8, pcr_imp10_8, on='Name', how='inner') #common in both
common_imp_var_8 = common_imp_var_8.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_8[['Name','Label','SVM coef_ Score','PCR coef_ Score']])



   Name                                              Label  SVM coef_ Score  \
0   M10                                           Creatine         0.069388   
1    M2                                         Creatinine         0.058710   
2   M35                             gamma-Glutamyl-leucine         0.056520   
3  M142                          Phosphatidylcholine(28:2)         0.056014   
4  M141  Ceramide phosphoethanolamine(35:2)|Sphingomyel...         0.053308   
5   M11                             L-Leucine|L-Norleucine         0.047938   
6   M24                           1,3,7-Trimethyluric acid         0.045943   

   PCR coef_ Score  
0         0.028100  
1         0.021007  
2         0.029296  
3         0.025117  
4         0.020239  
5         0.022664  
6         0.022954  


#9. ML methods on  dataset with 50% data points removed. Drop all rows with NaN.


In [ ]:
DataTable_st2_NaN_rm = DataTable_st2.dropna()
DataTable_st2_NaN_rm

Empty DataFrame
Columns: [Idx, SampleID, Class, Sex, M1, M2, M3, M4, M5, M6, M7, M8, M9, M10, M11, M12, M13, M14, M15, M16, M17, M18, M19, M20, M21, M22, M23, M24, M25, M26, M27, M28, M29, M30, M31, M32, M33, M34, M35, M36, M37, M38, M39, M40, M41, M42, M43, M44, M45, M46, M47, M48, M49, M50, M51, M52, M53, M54, M55, M56, M57, M58, M59, M60, M61, M62, M63, M64, M65, M66, M67, M68, M69, M70, M71, M72, M73, M74, M75, M76, M77, M78, M79, M80, M81, M82, M83, M84, M85, M86, M87, M88, M89, M90, M91, M92, M93, M94, M95, M96, ...]
Index: []

[0 rows x 193 columns]

The same reason as 6.

There will be no dataset left if all rows with NaN are removed since after changing 50% of data to be NaN, every row got at least one NaN.

#10. ML methods on 10% Noisy Data 


###10(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st3[(DataTable_st3.Class == 1) | (DataTable_st3.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)


In [ ]:

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
#XTrainLog = np.log(XTrain)                                          
#XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              


In [ ]:

# Extract Test Data
XTest = DataTest[PeakList]                                    
#XTestLog = np.log(XTest) #converted to log values                                         
#XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            


In [ ]:
XTrainLog

M1        M2        M3        M4        M5        M6        M7  \
767  2.723068  2.660840  2.578657  2.589525  2.471961  2.713593  2.839019   
270  2.708393  2.673669  2.538850  2.450446  2.430029  2.692303  2.826350   
566  2.721657  2.678912  2.442695  2.433571  2.145413  2.719601       NaN   
927  2.712441  2.660890  2.484418  2.504155  2.449052  2.732852  2.875316   
480  3.359808  2.690898  2.657447  2.510632  2.458028  2.753938  2.868274   
..        ...       ...       ...       ...       ...       ...       ...   
281  2.711171  2.667876  2.586820  2.531442  2.491026  2.740895  2.831178   
763  2.741045  2.664314  2.549687  2.413823  2.478461  2.744033  2.865735   
884  2.702755  2.678993  2.307110  2.405712  2.438256  2.702436  2.982917   
187  2.713234  2.706427  2.462703  2.474503  3.530230  2.745325  2.820132   
378  2.711409  2.654460  2.639980  2.401728  2.431215  2.659485       NaN   

           M8        M9       M10  ...      M180      M181      M182  \
767  2.493929  2.059079  2.923822  ...  3.017031  3.022846  3.051298   
270 -0.528611  2.094982  3.766818  ...  3.075476  3.071418  3.097612   
566  2.491424  2.033908  2.715410  ...  3.057609  3.038974  3.052960   
927  2.503415  2.041502  2.610277  ...  3.050641  3.011542  0.845087   
480  2.514198  2.104579  2.708075  ...  2.525622  3.076431  3.074085   
..        ...       ...       ...  ...       ...       ...       ...   
281  2.494273  2.013102  2.748885  ...  3.075653  3.046624  3.044789   
763  2.491669  2.015328  2.741367  ...  3.090662  3.087135  3.054506   
884  2.386480  2.019110  2.723613  ...  3.070352  3.032367  3.061232   
187  2.499350  2.174529       NaN  ...  3.078690  1.297210  3.100081   
378  2.482967  2.042007  2.658155  ...  3.071859  2.112168  3.038795   

         M183      M184      M185      M186      M187      M188      M189  
767  2.992289  2.751841  2.409573  2.852073  2.956453  2.925685  3.131611  
270  3.066504  2.826777  2.574689  2.887538  2.988367  3.008276       NaN  
566  3.007776  2.677727  2.468675  2.871235  2.964644  2.942871       NaN  
927  3.046202  2.812208  2.516728  2.831214       NaN  2.972494  2.513985  
480  3.031015  2.783980  2.491309  2.898381  2.941455  3.002839  2.464792  
..        ...       ...       ...       ...       ...       ...       ...  
281  3.002231  2.679133  2.345298  2.834104  2.920996  2.920965  2.428836  
763  3.009530  2.777700  3.282077  2.909513  2.988426  2.996863  2.509119  
884  2.993262  3.628971  2.370178  2.869324  2.958214  2.923389  2.491615  
187  3.081142  2.810355  2.557004       NaN  2.983738  3.040718  2.551881  
378  3.014438  4.109572  2.466015  2.909636  2.969384  2.956535  2.489610  

[582 rows x 189 columns]

###10(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrain,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

Number of cores set to: 2
Running ...






1/2:   0%|          | 0/40 [00:00<?, ?it/s]



1/2:  10%|█         | 4/40 [00:06<00:55,  1.55s/it]



1/2:  15%|█▌        | 6/40 [00:06<00:32,  1.04it/s]



1/2:  30%|███       | 12/40 [00:06<00:10,  2.79it/s]



1/2:  50%|█████     | 20/40 [00:06<00:03,  5.87it/s]



1/2: 100%|██████████| 40/40 [00:06<00:00,  5.80it/s]




2/2:   0%|          | 0/400 [00:00<?, ?it/s]

TerminatedWorkerError was raised due to excessive memory usage. n_cores was reduced to 1.







2/2:   0%|          | 0/400 [00:00<?, ?it/s]

InvalidIndexError: ignored

In [ ]:
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrain,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)                                 

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2') 

###10(c) Build Models & Evaluate


In [ ]:
#1. pcr
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest)

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

###10(d) Bootstrap Evaluation


In [ ]:
# Extract X Data
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

In [ ]:
#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest) 

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 

###10(e) Important features


In [ ]:

coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_10=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_10 

In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_10=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_10 

In [ ]:
common_imp_var_10 = pd.merge(svm_imp10_10, pcr_imp10_10, on='Name', how='inner') #common in both
common_imp_var_10 = common_imp_var_10.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_10[['Name','Label','SVM coef_ Score','PCR coef_ Score']])

#11. ML methods on 50% Noisy Data 

###11(a) Extract X and Y


In [ ]:
# Extract PeakList 
PeakList = PeakTable['Name']  

# Select Subset of Data 
DataTable2 = DataTable_st4[(DataTable_st4.Class == 1) | (DataTable_st4.Class == 0)]

# Create a Binary Y Vector 
Outcomes = DataTable2['Class']
Y = Outcomes.values 

# Split Data into Train (2/3) and Test (1/3)
DataTrain, DataTest, YTrain, YTest = train_test_split(DataTable2, Y, test_size=1/3, stratify=Y, random_state=8)

# Extract Train Data 
XTrain = DataTrain[PeakList] #the values of column "Name" in PeakTable(now present in PeakList) are the columnnames in Datatable                                    
XTrainLog = np.log(XTrain)                                          
XTrainScale, mu, sigma = cb.utils.scale(XTrainLog, method='auto', return_mu_sigma=True)              
XTrainKnn = cb.utils.knnimpute(XTrainScale, k=3)    

# Extract Test Data
XTest = DataTest[PeakList]                                    
XTestLog = np.log(XTest) #converted to log values                                         
XTestScale = cb.utils.scale(XTestLog, method='auto', mu=mu, sigma=sigma) #scaled such that x = (x- mu)/sigma            
XTestKnn = cb.utils.knnimpute(XTestScale, k=3) #imputed with knn weighted mean                           



###11(b) Hyperparameter Optimisation for PCR and Random Forest


In [ ]:
#-----------------PCR--------------------------
# Parameter Dictionary
param_dict_pcr = {'n_components': [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40]}                  

# Initialise
cv_pcr = cb.cross_val.KFold(model=cb.model.PCR,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_pcr,                   
                        folds=5,
                        n_mc=10)                                

# Run and Plot
cv_pcr.run()
cv_pcr.plot(metric='auc')  
cv_pcr.plot(metric='r2q2')

In [ ]:
#----------------SVM--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.001, 0.01, 0.1, 1, 10]
param_dict_svm = dict(C=C_range, kernel="linear")               

# Initialise
cv_svm = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict_svm,                   
                        folds=5,
                        n_mc=10)                            

# Run and Plot
cv_svm.run()  
cv_svm.plot(metric='auc')
cv_svm.plot(metric='r2q2')

In [ ]:
#----------------SVM(continued)--------------------------
# Parameter Dictionary
C_range = [0.0001, 0.0002, 0.0004, 0.0006, 0.0008, 0.001, 0.002, 0.004, 0.006, 0.008, 0.01]
param_dict = dict(C=C_range, kernel="linear")               

# Initialise
cv = cb.cross_val.KFold(model=cb.model.SVM,                      
                        X=XTrainKnn,                                 
                        Y=YTrain,                               
                        param_dict=param_dict,                   
                        folds=5,
                        n_mc=10)   

# Run and Plot
cv.run()  
cv.plot(metric='auc')
cv.plot(metric='r2q2')

###11(c) Build Models & Evaluate




In [ ]:
model_pcr = cb.model.PCR(n_components=18) 

YPredTrain = model_pcr.train(XTrainKnn, YTrain)
YPredTest = model_pcr.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest] 

# Evaluate
model_pcr.evaluate(testset=EvalTest) 

In [ ]:
# 2. Build Model for SVM
model_svm = cb.model.SVM(C=0.0006, kernel="linear")     
YPredTrain = model_svm.train(XTrainKnn, YTrain)
YPredTest = model_svm.test(XTestKnn)

# Put YTrain and YPredTrain in a List
EvalTrain = [YTrain, YPredTrain]

# Put YTest and YPrestTest in a List
EvalTest = [YTest, YPredTest]

# Evaluate Model (include Test Dataset)
model_svm.evaluate(testset=EvalTest) 

###11(d) Bootstrap Evaluation

In [ ]:
XBoot = DataTable2[PeakList]
XBootLog = np.log(XBoot)
XBootScale = cb.utils.scale(XBootLog, method='auto')
XBootKnn = cb.utils.knnimpute(XBootScale, k=3)

#-------------------PCR-----------------------
YPredBoot = model_pcr.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_pcr = cb.bootstrap.Per(model_pcr, bootnum=100) 
bootmodel_pcr.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_pcr.evaluate(trainset=EvalTrain, testset=EvalTest) 

NameError: ignored

In [ ]:
#-------------------SVM-----------------------

YPredBoot = model_svm.train(XBootKnn, Y)

# Build Boostrap Models
bootmodel_svm = cb.bootstrap.Per(model_svm, bootnum=100) 
bootmodel_svm.run()

# Boostrap Evaluate Model (include Test Dataset)
bootmodel_svm.evaluate(trainset=EvalTrain, testset=EvalTest) 

###11(e) Important features


In [ ]:
coef_pcr=model_pcr.model.coef_
coef_pcr=coef_pcr.transpose()
coef_df=pd.DataFrame(coef_pcr,index=range(1,coef_pcr.size+1),columns=['Importance'])
coeflbl_pcr=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_pcr['Importance'] = abs(coeflbl_pcr['Importance']) # because both +ve and -ve values have same magnitude
pcr_imp10_11=coeflbl_pcr.sort_values(by='Importance', ascending=False)[:10]
pcr_imp10_11 


In [ ]:
coef_svm=model_svm.model.coef_
coef_svm=coef_svm.transpose()
coef_df=pd.DataFrame(coef_svm,index=range(1,coef_svm.size+1),columns=['Importance'])
coeflbl_svm=pd.concat([PeakTable,coef_df],axis=1)
coeflbl_svm['Importance'] = abs(coeflbl_svm['Importance']) # because both +ve and -ve values have same magnitude
svm_imp10_11=coeflbl_svm.sort_values(by='Importance', ascending=False)[:10]
svm_imp10_11 


In [ ]:
common_imp_var_11 = pd.merge(svm_imp10_11, pcr_imp10_11, on='Name', how='inner') #common in both
common_imp_var_11 = common_imp_var_11.rename(columns={'Label_x' :'Label', 'Importance_y': 'PCR coef_ Score', 'Importance_x': 'SVM coef_ Score'})
print(common_imp_var_11[['Name','Label','SVM coef_ Score','PCR coef_ Score']])

